# `l2hmc`-qcd

- For 4D $SU(3)$ $\langle U_{P}\rangle \approx 0.6$

- From Xiao-Yong's code, try exporting lattice, and:
    1. loading in here to use as starting point
    2. Comparing against
- Identify step where `np.nan` enters in tf and find where its coming from

## Imports / Setup

In [1]:
!nvidia-smi

Tue Aug 16 11:16:44 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.129.06   Driver Version: 470.129.06   CUDA Version: 11.4     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A100-SXM...  On   | 00000000:07:00.0 Off |                    0 |
| N/A   22C    P0    55W / 400W |      0MiB / 40536MiB |      0%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
|   1  NVIDIA A100-SXM...  On   | 00000000:0F:00.0 Off |                    0 |
| N/A   

In [2]:
!unset TF_XLA_FLAGS KMP_SETTINGS KMP_AFFINITY KMP_BLOCKTIME
import os
os.environ['CUDA_VISIBLE_DEVICES'] = '7'

from __future__ import absolute_import, print_function, annotations, division

# automatically detect and reload local changes to modules
%load_ext autoreload
%autoreload 2

# unset verbose TF XLA Flags
!unset TF_XLA_FLAGS
!unset KMP_AFFINITY KMP_SETTINGS

import os

import hydra
import torch
import tensorflow as tf
tf.config.run_functions_eagerly(True)
import numpy as np

torch.cuda.set_per_process_memory_fraction(0.9)
    
from l2hmc.main import setup, setup_tensorflow, setup_torch

os.environ['OMP_NUM_THREADS'] = '8'

_ = setup_torch(
    precision='float64',
    seed=1234,
)

_ = setup_tensorflow(
    precision='float64',
)

from hydra.core.global_hydra import GlobalHydra
from l2hmc.utils.rich import print_config

import logging

log = logging.getLogger()
log.setLevel('INFO')

wblog = logging.getLogger('wandb')
wblog.setLevel('INFO')
from rich.console import Console
console = Console(log_path=False)

--------------------------------------------------------------------------

  Local host:   thetagpu19
  Local device: mlx5_0
--------------------------------------------------------------------------
Using: float64 precision


In [3]:
import horovod.tensorflow as hvdtf
import horovod.torch as hvdpt

hvdtf.size()
hvdpt.size()

1

In [4]:
from l2hmc.experiment.pytorch.experiment import Experiment as ptExperiment
from l2hmc.experiment.tensorflow.experiment import Experiment as tfExperiment

def get_lattice_metrics(experiment: ptExperiment | tfExperiment, beta: float = 1.) -> dict:
    if experiment.cfg.framework == 'pytorch':
        assert isinstance(experiment, ptExperiment)
    if experiment.cfg.framework == 'tensorflow':
        assert isinstance(experiment, tfExperiment)
    state = experiment.trainer.dynamics.random_state(beta)
    metrics = experiment.lattice.calc_metrics(state.x)
    return metrics

In [5]:
from typing import Optional
import rich

from l2hmc.configs import State

console = rich.console.Console(log_path=False, force_jupyter=True)

def grab(x: torch.Tensor | tf.Tensor):
    try:
        return x.numpy()
    except:
        return x.detach().cpu().numpy()
        

def check_diff(x, y, name: Optional[str] = None):
    if isinstance(x, State):
        xd = {'x': x.x, 'v': x.v, 'beta': x.beta}
        yd = {'x': y.x, 'v': y.v, 'beta': y.beta}
        check_diff(xd, yd, name=f'State')
        
    elif isinstance(x, dict) and isinstance(y, dict):
        for (kx, vx), (ky, vy) in zip(x.items(), y.items()):
            check_diff(vx, vy, name=kx)
            
    elif isinstance(x, (list, tuple)) and isinstance(y, (list, tuple)):
        assert len(x) == len(y)
        for idx in range(len(x)):
            check_diff(x[idx], y[idx], name=f'{name}, {idx}')
            
    else:
        x = grab(x)
        y = grab(y)
        #if isinstance(x, torch.Tensor):
        #    x = x.detach().numpy()
        #if isinstance(y, torch.Tensor):
        #    y = y.detach().numpy()

        #if isinstance(x, tf.Tensor):
        #    x = x.numpy()
        #if isinstance(y, tf.Tensor):
        #    y = y.numpy()

        dstr = []
        if name is not None:
            dstr.append(f"'{name}''")
        dstr.append(f'  sum(diff): {(x - y).sum()}')
        dstr.append(f'  min(diff): {(x - y).min()}')
        dstr.append(f'  max(diff): {(x - y).max()}')
        dstr.append(f'  mean(diff): {(x - y).mean()}')
        dstr.append(f'  std(diff): {(x - y).std()}')
        dstr.append(f'  np.allclose: {np.allclose(x, y)}')
        console.log('\n'.join(dstr))

In [8]:
 def zero_weights(model):
    for layer in model.layers:
        weights = layer.get_weights()
        zeros = []
        for w in weights:
            console.log(f'Zeroing layer for: {layer} in {model}')
            zeros.append(np.zeros_like(w))
            
        layer.set_weights(zeros)
        #if len(weights) > 0:
        #    layer.set_weights([
        #        np.zeros_like(layer.get_weights()[0]),
        #        np.zeros_like
        #    ])
        #    w, b = weights
        #    zw = np.zeros_like(w)
        #    zb = np.zeros_like(b)
        #    console.log(f'Zeroing layer for: {layer} in {model}')
        #    layer.set_weights([w, b])
            
    return model

In [9]:
def check_weights(mpt, mtf):
    wpt = mpt.weight
    bpt = mpt.bias
    wtf, btf = mtf.get_weights()
    try:
        check_diff(
            wpt, wtf
        )
    except ValueError:
        check_diff(
            wpt.T, wtf
        )
        
    check_diff(
        bpt, btf
    )

In [10]:
from l2hmc.group.u1.pytorch.group import U1Phase as ptU1Phase

def update_v_fwd_pt(dynamics, step, state) -> tuple[State, torch.Tensor]:
    eps = dynamics.veps[str(step)]
    force = dynamics.grad_potential(state.x, state.beta)
    s, t, q = dynamics._call_vnet(step, (state.x, force))
    jac = eps * s / 2.
    logdet = jac.sum(dim=1)
    exp_s = jac.exp()
    exp_q = (eps * q).exp()
    vf = exp_s * state.v - 0.5 * eps * (force * exp_q + t)
    return State(state.x, vf, state.beta), logdet

def update_x_fwd_pt(dynamics, step, state, first = True, m: Optional[Tensor] = None):
    eps = dynamics.xeps['0']
    if m is None:
        m, mb = dynamics._get_mask(step)
    else:
        mb = torch.ones_like(m) - m
        
    xm_init = m * state.x
    s, t, q = dynamics._call_xnet(step, (xm_init, state.v), first=first)
    s = eps * s
    q = eps * q
    exp_s = s.exp()
    exp_q = q.exp()
    if dynamics.config.use_ncp:
        halfx = state.x / 2.
        _x = 2. * (halfx.tan() * exp_s).atan()
        xp = _x + eps * (state.v * exp_q + t)
        xf = xm_init + (mb * xp)
        cterm = halfx.cos() ** 2
        sterm = (exp_s * halfx.sin()) ** 2
        logdet_ = (exp_s / (cterm + sterm)).log()
        logdet = (mb * logdet_).sum(dim=1)
    else:
        xp = state.x * exp_s + eps * (state.v * exp_q + t)
        xf = xm_init + (mb * xp)
        logdet = (mb * s).sum(dim=1)
        
    xf = dynamics.g.compat_proj(xf)
    return State(x=xf, v=state.v, beta=state.beta), logdet

In [11]:
from l2hmc.group.u1.tensorflow.group import U1Phase as tfU1Phase

def update_v_fwd_tf(dynamics, step, state) -> tuple[State, tf.Tensor]:
    eps = dynamics.veps[step]
    force = dynamics.grad_potential(state.x, state.beta)
    s, t, q = dynamics._call_vnet(step, (state.x, force), training=False)
    jac = eps * s / 2.
    logdet = tf.reduce_sum(jac, axis=1)
    exp_s = tf.exp(jac)
    exp_q = tf.exp(eps * q)
    vf = exp_s * state.v - 0.5 * eps * (force * exp_q + t)
    return State(state.x, vf, state.beta), logdet


def update_x_fwd_tf(dynamics, step, state, first=True, m: Optional[Tensor] = None):
    eps = dynamics.xeps[step]
    if m is None:
        m, mb = dynamics._get_mask(step)
    else:
        mb = tf.ones_like(m) - m
        
    xm_init = tf.multiply(m, state.x)
    s, t, q = dynamics._call_xnet(step, (xm_init, state.v), first=first, training=False)
    s = eps * s
    q = eps * q
    exp_s = tf.exp(s)
    exp_q = tf.exp(q)
    TWO = tf.constant(2.0, dtype=TF_FLOAT)
    if dynamics.config.use_ncp:
        halfx = state.x / TWO
        _x = TWO * tf.math.atan(tf.math.tan(halfx) * exp_s)
        xp = _x + eps * (state.v * exp_q + t)
        xf = xm_init + (mb * xp)
        cterm = tf.math.square(tf.math.cos(halfx))
        sterm = (exp_s * tf.math.sin(halfx)) ** 2
        logdet_ = tf.math.log(exp_s / (cterm + sterm))
        logdet = tf.reduce_sum(mb * logdet_, axis=1)
    else:
        xp = state.x * exp_s + eps * (state.v * exp_q + t)
        xf = xm_init + (mb * xp)
        logdet = tf.reduce_sum((mb * s), axis=1)
        
    xf = dynamics.g.compat_proj(xf)
    return State(x=xf, v=state.v, beta=state.beta), logdet

In [12]:
from l2hmc.lattice.su3.pytorch.lattice import LatticeSU3 as LatticeSU3pt
from l2hmc.lattice.su3.tensorflow.lattice import LatticeSU3 as LatticeSU3tf

import l2hmc.group.su3.pytorch.group as gpt
import l2hmc.group.su3.tensorflow.group as gtf

In [13]:
from __future__ import absolute_import, print_function, annotations, division
import os
import hydra

from typing import Optional
from pathlib import Path

from omegaconf import OmegaConf
from hydra import (
    initialize,
    initialize_config_module,
    initialize_config_dir,
    compose
)

from l2hmc.common import get_timestamp
from l2hmc.configs import CONF_DIR
from l2hmc.experiment.pytorch.experiment import Experiment as ptExperiment
from l2hmc.experiment.tensorflow.experiment import Experiment as tfExperiment
from hydra.core.global_hydra import GlobalHydra

from l2hmc.utils.rich import print_config

In [14]:
from l2hmc.distributions.pytorch.haarSUN import HaarSUN as HaarSUNpt
hSU3 = HaarSUNpt(3)

In [15]:
ptsu3 = gpt.SU3()
tfsu3 = gtf.SU3()

## Simple method for running generic HMC

In [16]:
import time
from rich.console import Console
from l2hmc.common import grab_tensor


console = Console(log_path=False)

def update_dict(
    new: dict,
    existing: Optional[dict] = None,
) -> tuple[list[str], dict]:
    existing = {} if existing is None else existing
    mstr = []
    for key, val in new.items():
        if isinstance(val, (torch.Tensor, tf.Tensor)):
            val = grab_tensor(val)
            
        if isinstance(val, list):
            if isinstance(val[0], torch.Tensor):
                val = grab_tensor(torch.stack(val))
            elif isinstance(val[0], tf.Tensor):
                val = grab_tensor(tf.stack(val))
            else:
                try:
                    val = np.stack(val)
                except Exception as e:
                    log.exception(e)
        else: 
            val = np.array(val)
            
        mstr.append(f'{key}={val.mean():.8f}')
        try:
            existing[key].append(val)
        except KeyError:
            existing[key] = [val]
            
    return mstr, existing
            
    
def run_hmc(
    experiment: ptExperiment | tfExperiment,
    beta: float = 1.0,
    nlog: int = 10,
    eps: Optional[float] = None,
    nsteps: Optional[int] = None,
    nleapfrog: Optional[int] = None,
    state: Optional[State] = None
) -> dict:
    """Run generic HMC using preconfigured Experiment."""
    metrics = {}
    lattice = experiment.trainer.lattice
    dynamics = experiment.trainer.dynamics
    if state is None:
        state = dynamics.random_state(beta)
    assert np.allclose(state.beta.numpy(), beta)
    console.log(f'checkSU(x): {dynamics.g.checkSU(state.x)}')
    #diffs = np.array([i.numpy() for i in dynamics.g.checkSU(state.x)])
    #console.log(f'checkSU:\n {diffs}')
    #state.x = dynamics.g.compat_proj(state.x)
    #diffs = np.array([i.numpy() for i in dynamics.g.checkSU(state.x)])
    #console.log(f'compat_proj(checkSU):\n {diffs}')
    for step in range(nsteps):
        t0 = time.time()
        state, metrics_ = dynamics.transition_kernel_hmc(state, eps, nleapfrog)
        dt = time.time() - t0
        _ = metrics_.pop('mc_states', None)
        lmetrics = lattice.calc_metrics(state.x)
        mstr, metrics = update_dict(metrics_, metrics)
        lmstr, metrics = update_dict(lmetrics, metrics)
        console.log(', '.join([
            f'step: {step}',
            f'dt: {dt:.4f}',
            *mstr,
            *lmstr,
        ]))
        #if step % 10 == 0:
        #    console.log(
        #        f'checkSU(x): {dynamics.g.checkSU(state.x)}'
        #    )
                
    return metrics

## Instantiate Configs

1. Initialize [`Hydra`](https://hydra.cc) by registering `CONF_DIR` as `config_dir`
2. Compose `conf/config.yaml` with user-specified `overrides` to create `DictConfig` for `Experiment`

# Set some reasonable defaults for `ExperimentConfig`:

**Note**: For the purposes of demonstrating functionality, we only consider a very simple `debug` example here

In [17]:
GlobalHydra.instance().clear()

defaults = [
    'steps.nera=8',
    'steps.nepoch=500',
    'steps.test=2000',
    'steps.print=100',
    'steps.log=10',
]

defaults_u1 = [
    *defaults,
    'dynamics.nchains=1024',
    'dynamics.nleapfrog=5',
    'dynamics.latvolume=[8, 8]',
    'network.units=[16, 16, 16, 16]',
    'annealing_schedule.beta_init=1.0',
    'annealing_schedule.beta_final=4.0',
]

defaults_su3 = [
    *defaults,
    'dynamics=su3',
    'dynamics.verbose=true',
    'dynamics.nchains=10',
    'steps.nera=0',
    'steps.nepoch=0',
    'steps.test=1000',
    'dynamics.nleapfrog=1',
    'network.units=[1]',
    'steps.print=1',
    'steps.log=1',
    'dynamics.latvolume=[8, 8, 8, 16]',
    'annealing_schedule.beta_init=6.0',
    'annealing_schedule.beta_final=6.0',
]

## Instantiate Experiments for Testing

In [18]:
import gc
gc.collect()
with torch.no_grad():
    torch.cuda.empty_cache()
    
torch.clear_autocast_cache()

In [19]:
from l2hmc.configs import get_experiment
GlobalHydra.instance().clear()

ptExpSU3 = get_experiment(
    overrides=[
        *defaults_su3,
        'framework=pytorch',
        'init_wandb=False',
        'init_aim=False',
    ]
)

08:50:29 WARNING  xdim: 262144                                                                            ]8;id=88015;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=803713;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#651\651]8;;\

         WARNING  group: SU3                                                                              ]8;id=371862;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=18274;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#652\652]8;;\

         WARNING  xshape: (10, 4, 8, 8, 8, 16, 3, 3)                                                      ]8;id=32310;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=16609;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#653\653]8;;\

         WARNING  latvolume: [8, 8, 8, 16]                                                                ]8;id=362900;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=653557;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#654\654]8;;\

         WARNING  xdim: 262144                                                                            ]8;id=507768;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=645729;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#651\651]8;;\

         WARNING  group: SU3                                                                              ]8;id=486065;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=155770;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#652\652]8;;\

         WARNING  xshape: (10, 4, 8, 8, 8, 16, 3, 3)                                                      ]8;id=95721;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=191984;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#653\653]8;;\

         WARNING  latvolume: [8, 8, 8, 16]                                                                ]8;id=748064;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=119970;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#654\654]8;;\

In [20]:
tfExpSU3 = get_experiment(
    overrides=[
        *defaults_su3,
        'framework=tensorflow',
        'init_wandb=False',
        'init_aim=False',
    ]
)

08:50:30 WARNING  xdim: 262144                                                                            ]8;id=886412;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=15328;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#651\651]8;;\

         WARNING  group: SU3                                                                              ]8;id=527521;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=510395;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#652\652]8;;\

         WARNING  xshape: (10, 4, 8, 8, 8, 16, 3, 3)                                                      ]8;id=923240;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=261963;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#653\653]8;;\

         WARNING  latvolume: [8, 8, 8, 16]                                                                ]8;id=67698;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=699668;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#654\654]8;;\

         WARNING  xdim: 262144                                                                            ]8;id=567372;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=956631;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#651\651]8;;\

         WARNING  group: SU3                                                                              ]8;id=488530;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=71900;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#652\652]8;;\

         WARNING  xshape: (10, 4, 8, 8, 8, 16, 3, 3)                                                      ]8;id=630680;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=707921;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#653\653]8;;\

         WARNING  latvolume: [8, 8, 8, 16]                                                                ]8;id=93248;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py\configs.py]8;;\:]8;id=540063;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/configs.py#654\654]8;;\

In [21]:
import numpy as np

from l2hmc.configs import State
from l2hmc.common import grab_tensor
from l2hmc.trainers.pytorch.trainer import Trainer as ptTrainer
from l2hmc.trainers.tensorflow.trainer import Trainer as tfTrainer
from typing import Any

dynamicstf = ptExpSU3.trainer.dynamics
latticetf = ptExpSU3.trainer.lattice

dynamics_tf = tfExpSU3.trainer.dynamics
lattice_tf = tfExpSU3.trainer.lattice

nsteps = 100
nleapfrog = 64
eps = (0.1 / 16)

def clear_cache():
    import gc
    gc.collect()
    with torch.no_grad():
        torch.cuda.empty_cache()
    torch.clear_autocast_cache()
    

def run_hmc(
        trainer,
        x: Any = None,
        beta: float = 6.0,
        eps: float = (0.1 / 64.0),
        nleapfrog: int = 64,
        neval: int = 100,
) -> dict:
    state = trainer.dynamics.random_state(beta=beta)
    if isinstance(trainer, ptTrainer):
        beta = torch.tensor(beta)
    elif isinstance(trainer, tfTrainer):
        beta = tf.constant(beta)
        
    if x is None:
        x = trainer.draw_x()
    
    metrics = {}
    energies = []
    for step in range(neval):
        clear_cache()
        t0 = time.time()
        x, metrics_ = trainer.hmc_step(
            (x, beta),
            eps=eps,
            nleapfrog=nleapfrog,
        )
        #state, metrics_ = dynamics.transition_kernel_hmc(
        #    state,
        #    eps,
        #    nleapfrog
        #)
        if step > 1:
            denergy = (
                grab_tensor(metrics['energy'][-1])
                - grab_tensor(metrics_['energy'])
            )
            metrics_['dH'] = denergy
            metrics_['expmdH'] = np.exp(-denergy)
            
        dt = time.time() - t0
        mstr, metrics = update_dict(metrics_, metrics)
        #_ = metrics_.pop('mc_states', None)
        #lmetrics = trainer.lattice.calc_metrics(x)
        #lmstr, metrics_ = update_dict(lmetrics, metrics_)
        #mstr, metrics = update_dict(metrics_, metrics)
        console.log(', '.join([
            f'step: {step}',
            f'dt: {dt:.4f}',
            *mstr,
            #*lmstr,
        ]))
        
    return metrics

In [53]:
clear_cache()

In [54]:
!nvidia-smi

Fri Aug  5 09:33:22 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.129.06   Driver Version: 470.129.06   CUDA Version: 11.4     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A100-SXM...  On   | 00000000:07:00.0 Off |                    0 |
| N/A   23C    P0    58W / 400W |      0MiB / 81251MiB |      0%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
|   1  NVIDIA A100-SXM...  On   | 00000000:0F:00.0 Off |                    0 |
| N/A   

In [46]:
xpt.shape

torch.Size([10, 4, 8, 8, 8, 16, 3, 3])

In [52]:
xpt = ptExpSU3.trainer.lattice.random()
xpt_ = torch.zeros_like(xpt)

clear_cache()

metrics_pt = run_hmc(
    ptExpSU3.trainer,
    beta=6.0,
    eps=0.00625,
    nleapfrog=128,
    neval=1000,
)

RuntimeError: CUDA out of memory. Tried to allocate 12.00 MiB (GPU 0; 79.35 GiB total capacity; 71.35 GiB already allocated; 6.16 GiB free; 71.41 GiB allowed; 71.40 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [44]:
xpt = ptExpSU3.trainer.lattice.random()
xpt_ = torch.zeros_like(xpt)

clear_cache()

metrics_pt = run_hmc(
    ptExpSU3.trainer,
    beta=6.0,
    eps=0.00000625,
    nleapfrog=16,
    neval=1000,
)

[08:57:48] step: 0, dt: 2.1097, energy=-69.53266047, logprob=-69.53266047, logdet=0.00000000,
           acc=0.96218272, sumlogdet=0.00000000, acc_mask=1.00000000, plaqs=-0.00034992,     
           sinQ=0.00045755, intQ=0.21362623, dQint=0.00013042, dQsin=0.00000028,             
           loss=99.98999764

[08:57:51] step: 1, dt: 2.0097, energy=21.26875813, logprob=21.26875813, logdet=0.00000000,  
           acc=0.94715239, sumlogdet=0.00000000, acc_mask=0.89999998, plaqs=-0.00034991,     
           sinQ=0.00045754, intQ=0.21362007, dQint=0.00012934, dQsin=0.00000028,             
           loss=99.98999766

[08:57:53] step: 2, dt: 2.0163, energy=41.25617144, logprob=41.25617144, logdet=0.00000000,  
           acc=0.92839180, sumlogdet=0.00000000, acc_mask=0.89999998, plaqs=-0.00034974,     
           sinQ=0.00045760, intQ=0.21365028, dQint=0.00012687, dQsin=0.00000027,             
           loss=99.98999767, dH=-19.98741331, expmdH=inf

[08:57:56] step: 3, dt: 2.0365, energy=12.78086713, logprob=12.78086713, logdet=0.00000000,  
           acc=0.92643767, sumlogdet=0.00000000, acc_mask=0.89999998, plaqs=-0.00034977,     
           sinQ=0.00045751, intQ=0.21360686, dQint=0.00014626, dQsin=0.00000031,             
           loss=99.98999760, dH=28.47530431, expmdH=22093360404534936084263591736699456155638
           9952554586734923945444284412504923552105845835962443716191034477890282391620215373
           9273251809625747738942050436377727927801994811967361923043625503039849776893423262
           182393646598257115136.00000000

[08:57:59] step: 4, dt: 2.0178, energy=43.61715084, logprob=43.61715084, logdet=0.00000000,  
           acc=0.97423969, sumlogdet=0.00000000, acc_mask=1.00000000, plaqs=-0.00034973,     
           sinQ=0.00045769, intQ=0.21368789, dQint=0.00020299, dQsin=0.00000043,             
           loss=99.98999751, dH=-30.83628371, expmdH=2787741360040643081111585301180870607690
           8520308157090563212222520398378018415363744998265483634143225870092944775696719991
           6325309630579545357231552976132672051298068220215720771897635316261134378905141318
           7756750709462058168511216339508442471722093292483254372484453627179219295294333445
           72391424.00000000

...

[09:28:49] step: 673, dt: 2.0200, energy=51.01461826, logprob=51.01461826, logdet=0.00000000,
           acc=0.96328968, sumlogdet=0.00000000, acc_mask=1.00000000, plaqs=-0.00034283,     
           sinQ=0.00045703, intQ=0.21338131, dQint=0.00012095, dQsin=0.00000026,             
           loss=99.98999766, dH=175.78965409, expmdH=inf

[09:28:52] step: 674, dt: 2.0209, energy=152.72078388, logprob=152.72078388,                 
           logdet=0.00000000, acc=0.99543828, sumlogdet=0.00000000, acc_mask=1.00000000,     
           plaqs=-0.00034269, sinQ=0.00045717, intQ=0.21344913, dQint=0.00014066,            
           dQsin=0.00000030, loss=99.98999765, dH=-101.70616562, expmdH=inf

[09:28:55] step: 675, dt: 2.0301, energy=209.04346190, logprob=209.04346190,                 
           logdet=0.00000000, acc=0.94883431, sumlogdet=0.00000000, acc_mask=0.89999998,     
           plaqs=-0.00034256, sinQ=0.00045739, intQ=0.21355151, dQint=0.00009654,            
           dQsin=0.00000021, loss=99.98999769, dH=-56.32267803, expmdH=inf

[09:28:58] step: 676, dt: 2.0152, energy=143.97633069, logprob=143.97633069,                 
           logdet=0.00000000, acc=0.92137206, sumlogdet=0.00000000, acc_mask=0.89999998,     
           plaqs=-0.00034246, sinQ=0.00045745, intQ=0.21357635, dQint=0.00007859,            
           dQsin=0.00000017, loss=99.98999762, dH=65.06713121, expmdH=17932349031747358788509
           5327701104286401637238230593761152158659753342986481484081753795386014941941086360
           3388137235411990545087893778432579286202406342268072677617885376121949855510933832
           1894402874015262024946120114066998435066793530999698027906115044297082370855912079
           360.00000000

KeyboardInterrupt: 

In [80]:
xtf = tf.constant(grab_tensor(xpt_))

metrics_tf = run_hmc(
    tfExpSU3.trainer,
    beta=6.0,
    eps=0.00625,
    nleapfrog=16,
    neval=100,
)

[08:39:17] step: 0, dt: 0.8759, energy=nan, logprob=nan, logdet=0.00000000, acc=0.00000000,  
           sumlogdet=0.00000000, acc_mask=0.00000000, plaqs=-625.68584978, sinQ=478.29348963,
           intQ=223309.49759055, dQint=0.00000000, dQsin=0.00000000, loss=nan

[08:39:18] step: 1, dt: 0.8493, energy=nan, logprob=nan, logdet=0.00000000, acc=0.00000000,  
           sumlogdet=0.00000000, acc_mask=0.00000000, plaqs=-625.68584978, sinQ=478.29348963,
           intQ=223309.49759055, dQint=0.00000000, dQsin=0.00000000, loss=nan

[08:39:19] step: 2, dt: 0.8599, energy=nan, logprob=nan, logdet=0.00000000, acc=0.00000000,  
           sumlogdet=0.00000000, acc_mask=0.00000000, plaqs=-625.68584978, sinQ=478.29348963,
           intQ=223309.49759055, dQint=0.00000000, dQsin=0.00000000, loss=nan, dH=nan,       
           expmdH=nan

[08:39:20] step: 3, dt: 0.8387, energy=nan, logprob=nan, logdet=0.00000000, acc=0.00000000,  
           sumlogdet=0.00000000, acc_mask=0.00000000, plaqs=-625.68584978, sinQ=478.29348963,
           intQ=223309.49759055, dQint=0.00000000, dQsin=0.00000000, loss=nan, dH=nan,       
           expmdH=nan

[08:39:22] step: 4, dt: 0.8448, energy=nan, logprob=nan, logdet=0.00000000, acc=0.00000000,  
           sumlogdet=0.00000000, acc_mask=0.00000000, plaqs=-625.68584978, sinQ=478.29348963,
           intQ=223309.49759055, dQint=0.00000000, dQsin=0.00000000, loss=nan, dH=nan,       
           expmdH=nan

[08:39:23] step: 5, dt: 0.8405, energy=nan, logprob=nan, logdet=0.00000000, acc=0.00000000,  
           sumlogdet=0.00000000, acc_mask=0.00000000, plaqs=-625.68584978, sinQ=478.29348963,
           intQ=223309.49759055, dQint=0.00000000, dQsin=0.00000000, loss=nan, dH=nan,       
           expmdH=nan

[08:39:24] step: 6, dt: 0.8443, energy=nan, logprob=nan, logdet=0.00000000, acc=0.00000000,  
           sumlogdet=0.00000000, acc_mask=0.00000000, plaqs=-625.68584978, sinQ=478.29348963,
           intQ=223309.49759055, dQint=0.00000000, dQsin=0.00000000, loss=nan, dH=nan,       
           expmdH=nan

KeyboardInterrupt: 

In [16]:
import gc
gc.collect()
with torch.no_grad():
    torch.cuda.empty_cache()

In [15]:
metrics_pt = run_hmc(
    ptExpSU3.trainer.dynamics,
    ptExpSU3.trainer.lattice,
    beta=6.0,
    eps=0.00001,
    nleapfrog=16,
    neval=100,
)

[08:48:15] step: 0, dt: 0.3028, energy=-257.96895769, logprob=-257.96895769,                 
           logdet=0.00000000, acc=1.00000000, sumlogdet=0.00000000, plaqs=-0.00011333,       
           sinQ=0.00163941, intQ=0.76542131, plaqs=-0.00011333, sinQ=0.00163941,             
           intQ=0.76542131

           step: 1, dt: 0.2490, energy=-258.08949517, logprob=-258.08949517,                 
           logdet=0.00000000, acc=1.00000000, sumlogdet=0.00000000, plaqs=-0.00011303,       
           sinQ=0.00164037, intQ=0.76586744, plaqs=-0.00011303, sinQ=0.00164037,             
           intQ=0.76586744

[08:48:16] step: 2, dt: 0.2419, energy=-258.15002294, logprob=-258.15002294,                 
           logdet=0.00000000, acc=1.00000000, sumlogdet=0.00000000, plaqs=-0.00011273,       
           sinQ=0.00164132, intQ=0.76631353, plaqs=-0.00011273, sinQ=0.00164132,             
           intQ=0.76631353

           step: 3, dt: 0.2405, energy=-258.15054067, logprob=-258.15054067,                 
           logdet=0.00000000, acc=0.97094312, sumlogdet=0.00000000, plaqs=-0.00011243,       
           sinQ=0.00164228, intQ=0.76675958, plaqs=-0.00011243, sinQ=0.00164228,             
           intQ=0.76675958

           step: 4, dt: 0.2427, energy=-258.09104806, logprob=-258.09104806,                 
           logdet=0.00000000, acc=0.91439020, sumlogdet=0.00000000, plaqs=-0.00011212,       
           sinQ=0.00164323, intQ=0.76720560, plaqs=-0.00011212, sinQ=0.00164323,             
           intQ=0.76720560

...

           step: 23, dt: 0.2796, energy=-245.55839878, logprob=-245.55839878,                
           logdet=0.00000000, acc=0.29236890, sumlogdet=0.00000000, plaqs=-0.00010634,       
           sinQ=0.00166137, intQ=0.77567221, plaqs=-0.00010634, sinQ=0.00166137,             
           intQ=0.77567221

           step: 24, dt: 0.2494, energy=-244.29865287, logprob=-244.29865287,                
           logdet=0.00000000, acc=0.27533881, sumlogdet=0.00000000, plaqs=-0.00010603,       
           sinQ=0.00166232, intQ=0.77611738, plaqs=-0.00010603, sinQ=0.00166232,             
           intQ=0.77611738

[08:48:22] step: 25, dt: 0.2479, energy=-242.97889293, logprob=-242.97889293,                
           logdet=0.00000000, acc=0.25930068, sumlogdet=0.00000000, plaqs=-0.00010573,       
           sinQ=0.00166327, intQ=0.77656250, plaqs=-0.00010573, sinQ=0.00166327,             
           intQ=0.77656250

           step: 26, dt: 0.2525, energy=-241.59911892, logprob=-241.59911892,                
           logdet=0.00000000, acc=0.24419674, sumlogdet=0.00000000, plaqs=-0.00010542,       
           sinQ=0.00166423, intQ=0.77700758, plaqs=-0.00010542, sinQ=0.00166423,             
           intQ=0.77700758

RuntimeError: CUDA out of memory. Tried to allocate 20.00 MiB (GPU 0; 79.35 GiB total capacity; 39.63 GiB already allocated; 37.51 GiB free; 39.67 GiB allowed; 39.66 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [ ]:
output_ptsu3 = ptExpSU3.evaluate(job_type='hmc')

In [24]:
ptExpSU3.trainer.eval(beta=6.0, nleapfrog=16, eps=(0.5/16), eval_steps=100)

17:27:07 WARNING  x.shape (original): torch.Size([5, 294912])                                             ]8;id=493711;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/trainers/pytorch/trainer.py\trainer.py]8;;\:]8;id=912458;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/trainers/pytorch/trainer.py#560\560]8;;\

         WARNING  x[:nchains].shape: torch.Size([5, 294912])                                              ]8;id=857047;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/trainers/pytorch/trainer.py\trainer.py]8;;\:]8;id=623814;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/trainers/pytorch/trainer.py#567\567]8;;\

RuntimeError: mat1 and mat2 shapes cannot be multiplied (5x294912 and 262144x16)

In [26]:
tfExpSU3.trainer.eval(beta=tf.constant(6.0), nleapfrog=16, eps=(0.5/16), eval_steps=100)

17:27:32 WARNING  x.shape (original): (5, 294912)                                                         ]8;id=459142;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/trainers/tensorflow/trainer.py\trainer.py]8;;\:]8;id=310041;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/trainers/tensorflow/trainer.py#474\474]8;;\

         WARNING  x[:nchains].shape: (5, 294912)                                                          ]8;id=288401;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/trainers/tensorflow/trainer.py\trainer.py]8;;\:]8;id=129894;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/trainers/tensorflow/trainer.py#480\480]8;;\

ValueError: in user code:

    File "/lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/trainers/tensorflow/trainer.py", line 392, in eval_step  *
        xout, metrics = self.dynamics(inputs, training=False)
    File "/lus/theta-fs0/software/thetagpu/conda/2022-07-01/mconda3/lib/python3.8/site-packages/keras/utils/traceback_utils.py", line 67, in error_handler  **
        raise e.with_traceback(filtered_tb) from None
    File "/tmp/__autograph_generated_filehdbt8hp9.py", line 37, in tf__call
        ag__.if_stmt(ag__.ld(self).config.merge_directions, if_body, else_body, get_state, set_state, ('do_return', 'retval_'), 2)
    File "/tmp/__autograph_generated_filehdbt8hp9.py", line 24, in if_body
        retval_ = ag__.converted_call(ag__.ld(self).apply_transition_fb, (ag__.ld(inputs),), dict(training=ag__.ld(training)), fscope)
    File "/tmp/__autograph_generated_file03musmn7.py", line 12, in tf__apply_transition_fb
        data = ag__.converted_call(ag__.ld(self).generate_proposal

In [38]:
run_hmc(
    experiment=ptExperiment,
    beta=6.0,
    eps=0.00001,
    nleapfrog=16,
)

AttributeError: type object 'Experiment' has no attribute 'trainer'

In [26]:
def plot_kernels(tensor, num_cols=8):
    if not tensor.ndim==4:
        raise Exception("assumes a 4D tensor")
    if not tensor.shape[-1]==3:
        raise Exception("last dim needs to be 3 to plot")
    num_kernels = tensor.shape[0]
    num_rows = 1+ num_kernels // num_cols
    fig = plt.figure(figsize=(num_cols,num_rows))
    for i in range(tensor.shape[0]):
        ax1 = fig.add_subplot(num_rows,num_cols,i+1)
        ax1.imshow(tensor[i])
        ax1.axis('off')
        ax1.set_xticklabels([])
        ax1.set_yticklabels([])

    plt.subplots_adjust(wspace=0.1, hspace=0.1)
    plt.show()

## Run HMC with $SU(3)$

In [ ]:
outputs['pytorch']['su3']['hmc'] = run_hmc(ptExpSU3, nlog=1, nsteps=50, eps=0.001, nleapfrog=4)

In [ ]:
hmetrics_pt = outputs['pytorch']['su3']['hmc']
hmetrics_pt.keys()

In [ ]:
from l2hmc.common import make_dataset


dset_pt = make_dataset(hmetrics_pt)

In [ ]:
from l2hmc.common import plot_dataset

_ = plot_dataset(dset_pt)

In [ ]:
outputs['pytorch']['su3']['hmc'] = ptExpSU3.evaluate(job_type='hmc')

In [ ]:
outputs['tensorflow']['su3']['hmc'] = run_hmc(tfExpSU3, nlog=1, nsteps=100, eps=0.00001, nleapfrog=8)

In [ ]:
outputs['pytorch']['su3']['hmc'] = ptexpsu3.evaluate(job_type='hmc')

# Debugging $SU(3)$

In [5]:
import l2hmc.group.su3.tensorflow.utils as gtfutils
import l2hmc.group.su3.pytorch.utils as gptutils

In [6]:
ptState = ptExpSU3.trainer.dynamics.random_state(6.)
tfState = tfExpSU3.trainer.dynamics.random_state(6.)

NameError: name 'ptExpSU3' is not defined

In [83]:
xpt = ptExpSU3.trainer.lattice.random()

In [7]:
import l2hmc.group.su3.pytorch.utils as gpt
import l2hmc.group.su3.tensorflow.utils as gtf
from l2hmc.common import grab_tensor, check_diff

Upt = xpt[0, 0, 0, 0, 0, 0][None, :]
Upt.shape

Utf = tf.constant(grab_tensor(Upt))

x1pt = torch.ones_like(xpt)
x1tf = tf.constant(grab_tensor(x1pt))

console.log(f'checkSU:\n {np.array([grab_tensor(i) for i in gpt.checkSU(Upt)])}')
console.log(f'checkSU:\n {np.array([i.numpy() for i in gtf.checkSU(Utf)])}')
console.log(f'projectU.real:\n {grab_tensor(gpt.projectU(Upt)).real}')
console.log(f'projectU.imag:\n {gtf.projectU(Utf).numpy().imag}')
console.log(f'projectSU.real:\n {grab_tensor(gpt.projectSU(Upt)).real}')
console.log(f'projectSU.imag:\n {gtf.projectSU(Utf).numpy().imag}')

NameError: name 'xpt' is not defined

In [8]:
check_diff(
    gptutils.projectU(Upt), gtfutils.projectU(Utf)
)
check_diff(
    gptutils.projectSU(Upt), gtfutils.projectSU(Utf)
)

dsupt = gptutils.checkSU(Upt)
dsutf = gtfutils.checkSU(Utf)

check_diff(dsupt, dsutf)

#console.log([i.round(5) for i in dsupt])
#console.log([i.round(5) for i in dsutf])

NameError: name 'Upt' is not defined

In [88]:
lattice_pt = ptExpSU3.trainer.lattice
lattice_tf = tfExpSU3.trainer.lattice

In [89]:
xtf = tf.constant(grab_tensor(xpt))
beta_tf = tf.constant(6.0)
beta_pt = torch.tensor(6.0)

In [92]:
xtf.shape

TensorShape([1, 4, 8, 8, 8, 16, 3, 3])

In [93]:
xpt.shape

torch.Size([1, 4, 8, 8, 8, 16, 3, 3])

In [94]:
lmetrics_pt = lattice_pt.calc_metrics(xpt, beta=beta_pt)
lmetrics_tf = lattice_tf.calc_metrics(xtf, beta=beta_tf)

lmetrics1_pt = lattice_pt.calc_metrics(x1pt, beta=beta_pt)
lmetrics1_tf = lattice_tf.calc_metrics(x1tf, beta=beta_tf)

In [95]:
check_diff(lmetrics_pt, lmetrics_tf)
check_diff(lmetrics1_pt, lmetrics1_tf)

08:39:45 INFO     'plaqs''                                                                                 ]8;id=722293;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=447012;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): -2.168404344971009e-19                                                                   
                    min(diff): -2.168404344971009e-19                                                                   
                    max(diff): -2.168404344971009e-19                                                                   
                    mean(diff): -2.168404344971009e-19                                                                  
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'sinQ''                                                                                  ]8;id=995628;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=211704;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): -6.505213034913027e-19                                                                   
                    min(diff): -6.505213034913027e-19                                                                   
                    max(diff): -6.505213034913027e-19                                                                   
                    mean(diff): -6.505213034913027e-19                                                                  
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'intQ''                                                                                  ]8;id=106213;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=415914;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): -2.220446049250313e-16                                                                   
                    min(diff): -2.220446049250313e-16                                                                   
                    max(diff): -2.220446049250313e-16                                                                   
                    mean(diff): -2.220446049250313e-16                                                                  
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'action''                                                                                ]8;id=204055;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=739099;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): 1.7053025658242404e-13                                                                   
                    min(diff): 1.7053025658242404e-13                                                                   
                    max(diff): 1.7053025658242404e-13                                                                   
                    mean(diff): 1.7053025658242404e-13                                                                  
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

08:39:46 INFO     'dsdx''                                                                                  ]8;id=929506;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=930457;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): 1.8970155307718173e-13j                                                                  
                    min(diff): (-1.3322676295501878e-15+2.220446049250313e-16j)                                         
                    max(diff): (1.3322676295501878e-15+2.220446049250313e-16j)                                          
                    mean(diff): 6.4324799627408085e-19j                                                                 
                    std(diff): 1.8311115889778852e-16                                                                   
                    np.allclose: True                                                                                   

         INFO     'plaqs''                                                                                 ]8;id=481894;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=524830;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): 0.0                                                                                      
                    min(diff): 0.0                                                                                      
                    max(diff): 0.0                                                                                      
                    mean(diff): 0.0                                                                                     
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'sinQ''                                                                                  ]8;id=247807;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=858292;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): 0.0                                                                                      
                    min(diff): 0.0                                                                                      
                    max(diff): 0.0                                                                                      
                    mean(diff): 0.0                                                                                     
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'intQ''                                                                                  ]8;id=836294;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=378802;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): 0.0                                                                                      
                    min(diff): 0.0                                                                                      
                    max(diff): 0.0                                                                                      
                    mean(diff): 0.0                                                                                     
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'action''                                                                                ]8;id=976250;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=900397;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): 0.0                                                                                      
                    min(diff): 0.0                                                                                      
                    max(diff): 0.0                                                                                      
                    mean(diff): 0.0                                                                                     
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'dsdx''                                                                                  ]8;id=215042;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=540052;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    sum(diff): 0j                                                                                       
                    min(diff): 0j                                                                                       
                    max(diff): 0j                                                                                       
                    mean(diff): 0j                                                                                      
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

In [ ]:
trainer_pt = ptExpSU3.trainer
trainer_tf = tfExpSU3.trainer

dynamics_pt = ptExpSU3.trainer.dynamics
dynamics_tf = tfExpSU3.trainer.dynamics

In [96]:
state_pt = dynamics_pt.random_state(6.0)
state_tf = State(
    x=tf.constant(grab_tensor(state_pt.x)),
    v=tf.constant(grab_tensor(state_pt.v)),
    beta=tf.constant(grab_tensor(state_pt.beta)),
)
action_pt = dynamics_pt.hamiltonian(state_pt)
action_tf = dynamics_tf.hamiltonian(state_tf)

NameError: name 'dynamics_pt' is not defined

In [97]:
out_pt = trainer_pt.hmc_step((state_pt.x, state_pt.beta), eps=0.001, nleapfrog=16)
out_tf = trainer_tf.hmc_step((state_tf.x, state_tf.beta), eps=0.001, nleapfrog=16)

NameError: name 'trainer_pt' is not defined

In [ ]:
%debug

In [ ]:
%

In [ ]:
out_

In [39]:
metrics_pt = {
    '_plaquettes': lattice_pt._plaquettes(xpt),
    #'plaqs': lattice_pt.plaqs(x=xpt),
    #'wilson_loops': lattice_pt.wilson_loops(xpt),
    #'_wilson_loops': lattice_pt._wilson_loops(xpt),
}

metrics_tf = {
    '_plaquettes': lattice_tf._plaquettes(xtf),
    #'plaqs': lattice_tf.plaqs(x=xtf),
    #'wilson_loops': lattice_tf.wilson_loops(xtf),
    #'_wilson_loops': lattice_tf._wilson_loops(xtf),
}

In [40]:
check_diff(
    lattice_pt._plaquettes(xpt),
    lattice_tf._plaquettes(xtf)
)

07:44:32 INFO       sum(diff): -2.168404344971009e-19                                                      ]8;id=616068;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=520703;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    min(diff): -2.168404344971009e-19                                                                   
                    max(diff): -2.168404344971009e-19                                                                   
                    mean(diff): -2.168404344971009e-19                                                                  
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

In [41]:
check_diff(
    lattice_pt.sin_charges(xpt),
    lattice_tf.sin_charges(xtf)
)

07:44:34 INFO       sum(diff): 5.963111948670274e-19                                                       ]8;id=171969;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=78980;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#114\114]8;;\
                    min(diff): 5.963111948670274e-19                                                                    
                    max(diff): 5.963111948670274e-19                                                                    
                    mean(diff): 5.963111948670274e-19                                                                   
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

In [ ]:
check_diff(
    lattice_pt.int_charges(xpt),
    lattice_tf.int_charges(xtf)
)

In [38]:
check_diff(
    lattice_pt.action(xpt, torch.tensor(1.0)),
    lattice_tf.action(xtf, tf.constant(1.0)),
)

09:24:27 INFO       sum(diff): 3.552713678800501e-14                                                       ]8;id=912458;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=857047;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    min(diff): 3.552713678800501e-14                                                                    
                    max(diff): 3.552713678800501e-14                                                                    
                    mean(diff): 3.552713678800501e-14                                                                   
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

In [ ]:
out = ptExpSU3.trainer.dynamics.hm

In [ ]:
outputs['pytorch']['su3']['hmc'] = ptExpSU3.evaluate(job_type='hmc', eps=0.0005, nleapfrog=128, eval_steps=1000)

In [ ]:
outputs['tensorflow']['su3']['hmc'] = tfExpSU3.evaluate(job_type='hmc', eps=0.0000125, nleapfrog=8, eval_steps=500)

In [39]:
check_diff(metrics_pt, metrics_tf)

09:25:57 INFO     '_plaquettes''                                                                           ]8;id=300032;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=842428;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): -6.505213034913027e-19                                                                   
                    min(diff): -6.505213034913027e-19                                                                   
                    max(diff): -6.505213034913027e-19                                                                   
                    mean(diff): -6.505213034913027e-19                                                                  
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

In [40]:
check_diff(xpt, xtf)

09:27:10 INFO       sum(diff): 0j                                                                          ]8;id=39840;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=230048;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    min(diff): 0j                                                                                       
                    max(diff): 0j                                                                                       
                    mean(diff): 0j                                                                                      
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

In [41]:
check_diff(lmetrics_pt, lmetrics_tf)

09:28:23 INFO     'plaqs''                                                                                 ]8;id=531329;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=869921;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): -6.505213034913027e-19                                                                   
                    min(diff): -6.505213034913027e-19                                                                   
                    max(diff): -6.505213034913027e-19                                                                   
                    mean(diff): -6.505213034913027e-19                                                                  
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'sinQ''                                                                                  ]8;id=91926;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=831306;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): 2.168404344971009e-19                                                                    
                    min(diff): 2.168404344971009e-19                                                                    
                    max(diff): 2.168404344971009e-19                                                                    
                    mean(diff): 2.168404344971009e-19                                                                   
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'intQ''                                                                                  ]8;id=978138;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=984580;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): 0.0                                                                                      
                    min(diff): 0.0                                                                                      
                    max(diff): 0.0                                                                                      
                    mean(diff): 0.0                                                                                     
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'action''                                                                                ]8;id=733360;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=332383;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): 1.9895196601282805e-13                                                                   
                    min(diff): 1.9895196601282805e-13                                                                   
                    max(diff): 1.9895196601282805e-13                                                                   
                    mean(diff): 1.9895196601282805e-13                                                                  
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'dsdx''                                                                                  ]8;id=320470;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=990957;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): -1.5357506932822673e-14j                                                                 
                    min(diff): (-1.7763568394002505e-15-2.220446049250313e-16j)                                         
                    max(diff): (1.7763568394002505e-15+0j)                                                              
                    mean(diff): -5.2074879736405004e-20j                                                                
                    std(diff): 1.8482278616737632e-16                                                                   
                    np.allclose: True                                                                                   

for key, val in lmetrics_pt.items():
    #try:
    console.log(f'(pytorch) {key}: {val.mean()}')
    console.log(f'(tensorflow) {key}: {lmetrics_tf[key].numpy().mean()}')
    console.log(f'sum(diff): {key}: {(grab_tensor(val) - lmetrics_tf[key].numpy()).sum()}')
    console.log(np.allclose(grab_tensor(val), lmetrics_tf[key].numpy()))
    #except:
    #    import pdb; pdb.set_trace()

In [ ]:
dynamics_pt = ptExpSU3.dynamics
dynamics_tf = tfExpSU3.dynamics

In [ ]:
from  l2hmc.configs import State

state_pt = dynamics_pt.random_state(6.0)
_x = tf.constant(state_pt.x.detach().numpy())
_v = tf.constant(state_pt.v.detach().numpy())
state_tf = State(_x, _v, beta_tf)

In [ ]:
state_tf.x.shape

In [ ]:
state_pt.x.shape

In [ ]:
state_tf_ = dynamics_tf.random_state(6.0)

In [ ]:
gtfutils.checkSU(state_tf_.x)

In [ ]:
gtfutils.checkSU(state_tf.x)

In [ ]:
state_tf1, metricstf1 = dynamics_tf.transition_kernel_hmc(state_tf, eps=0.0001, nleapfrog=10)
state_pt1, metricspt1 = dynamics_pt.transition_kernel_hmc(state_pt, eps=0.0001, nleapfrog=10)

lmetricspt1 = lattice_pt.calc_metrics(state_pt1.x, state_pt1.beta)
lmetricstf1 = lattice_tf.calc_metrics(state_tf1.x, state_tf1.beta)

In [ ]:
dynamics_pt = ptExpSU3.dynamics
dynamics_tf = tfExpSU3.dynamics

In [ ]:
_ = metricspt1.pop('mc_states', None)
_ = metricstf1.pop('mc_states', None)

for key, val in metricspt1.items():
    console.log(f'(pytorch) {key}: {val.mean()}')
    console.log(f'(tensorflow) {key}: {metricstf1[key].numpy().mean()}')
    console.log(f'sum(diff): {key}: {(val.detach().numpy() - metricstf1[key].numpy()).sum()}')
    console.log(np.allclose(val.detach().numpy(), metricstf1[key].numpy()))
    
for key, val in lmetricspt1.items():
    console.log(f'(pytorch) {key}: {val.mean()}')
    console.log(f'(tensorflow) {key}: {lmetricstf1[key].numpy().mean()}')
    allclose = np.allclose(val.detach().numpy(), lmetricstf1[key].numpy())
    diff_sum = (val.detach().numpy() - lmetricstf1[key].numpy()).sum()
    console.log(' '.join([
        f'{allclose}',
        f'sum(diff): {diff_sum}'
    ]))

In [ ]:
metrics_pt = run_hmc(ptExpSU3, beta=6.0, eps=0.00001, nleapfrog=8, nsteps=100)

In [ ]:
metrics_pt = run_hmc(ptExpSU3, beta=0.7796, eps=1.0/32.0, nleapfrog=32, nsteps=100)

In [ ]:
#state_tf.beta = tf.constant(0.7796)
_state_tf = State(x=state_tf.x, v=state_tf.v, beta=tf.constant(0.7796))
metrics_tf = run_hmc(tfExpSU3, beta=0.7796, eps=0.0001, nleapfrog=64, nsteps=100, state=_state_tf)

In [ ]:
metrics_tf = run_hmc(tfExpSU3, beta=0.7796, eps=0.00001, nleapfrog=64, nsteps=10)

In [ ]:
%debug

In [ ]:
metrics_tf = run_hmc(tfExpSU3, beta=0.7796, eps=0.00001, nleapfrog=64, nsteps=10)

In [ ]:
metrics_tf = run_hmc(tfExpSU3, beta=0.7796, eps=0.000001, nleapfrog=32, nsteps=10)

In [ ]:
metrics_tf = test_hmc(state_tf, dynamics_tf, lattice_tf, eps=0.000001, nleapfrog=64)

In [ ]:
metrics_pt = test_hmc(state_pt, dynamics_pt, lattice_pt, eps=0.00001, nleapfrog=32)

In [ ]:
lmetricstf1 = lattice_tf.calc_metrics(state_tf1.x, beta_tf)
lmetricspt1 = lattice_pt.calc_metrics(state_pt1.x, beta_pt)

In [ ]:
from l2hmc.configs import MonteCarloStates

_ = metricspt1.pop('mc_states', None)
_ = metricstf1.pop('mc_states', None)

print('PYTORCH')
print('-------')
for key, val in metricspt1.items():
    print(f'{key}: {val.mean()}')
for key, val in lmetricspt1.items():
    print(f'{key}: {val.mean()}')
    
print('TENSORFLOW')
print('----------')
for key, val in metricstf1.items():
    print(f'{key}: {val.numpy().mean()}')
for key, val in lmetricstf1.items():
    print(f'{key}: {val.numpy().mean()}')

In [ ]:
def run_hmc(
    experiment,
    nleapfrog,
    eps,
    xinit: Tens
)

In [ ]:
run_hmc(tfExpSU3, beta=0.7796, x=state_tf.x, eps=0.00001, nleapfrog=10)  # , eps=4.0/128, nleapfrog=128, nsteps=1000, nlog=1)

In [ ]:
run_hmc()

In [ ]:
lmetricstf1 = lattice_tf.calc_metrics(xtf1, beta_tf)

lmetricspt1 = lattice_pt.calc_metrics(xpt1, beta_pt)

In [ ]:
xtf1, metricstf1 = tfExpSU3.dynamics.apply_transition_hmc((xtf, beta_tf), eps=0.00001, nleapfrog=10)

In [ ]:
xpt1, metricspt1 = ptExpSU3.dynamics.apply_transition_hmc((xpt, beta_pt), eps=0.00001, nleapfrog=10)

In [ ]:
print('PYTORCH')
print('-------')
for key, val in lmetricspt1.items():
    print(f'{key}: {val.mean()}')
    
print('TENSORFLOW')
print('----------')
for key, val in lmetricstf1.items():
    print(f'{key}: {val.numpy().mean()}')

In [ ]:
np.allclose(state_pt.x.numpy(), state_tf.x.numpy())

In [ ]:
ept = dynamics_pt.hamiltonian(state_pt)
etf = dynamics_tf.hamiltonian(state_tf)

print(f'ept: {ept}')
print(f'etf: {etf}')

In [ ]:
dept = dynamics_pt.grad_potential(state_pt.x, state_pt.beta)
detf = dynamics_tf.grad_potential(state_tf.x, state_tf.beta)

In [ ]:
np.allclose(dept.numpy(), detf.numpy())

In [ ]:
pxpt = dynamics_pt.

In [ ]:
(xtf1.numpy() - xpt1.detach().numpy()).mean()

In [ ]:
np.allclose(xtf1.numpy(), xpt1.detach().numpy())

In [ ]:
tf.subtract(tf.constant(1.), tf.constant(2.))

In [ ]:
console.log(f'checkSU:\n {np.array([i.numpy() for i in gptutils.checkSU(Upt)])}')
console.log(f'projectU.real:\n {gptutils.projectU(Upt).numpy().real}')
console.log(f'projectU.imag:\n {gptutils.projectU(Upt).numpy().imag}')
console.log(f'projectSU.real:\n {gptutils.projectSU(Upt).numpy().real}')
console.log(f'projectSU.imag:\n {gptutils.projectSU(Upt).numpy().imag}')

In [ ]:
run_hmc(tfExpSU3, beta=0.7796, x=gtfutils.projectSU(tf.constant(xpt.numpy())), eps=0.00001, nleapfrog=16)  # , eps=4.0/128, nleapfrog=128, nsteps=1000, nlog=1)

In [ ]:
run_hmc(ptExpSU3, beta=0.7796, x=gptutils.projectSU(xpt), eps=0.00001, nleapfrog=16)  # , eps=4.0/128, nleapfrog=128, nsteps=1000, nlog=1)

In [47]:
check_diff(xpt, xtf)

09:36:23 INFO       sum(diff): 0j                                                                          ]8;id=204055;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=739099;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    min(diff): 0j                                                                                       
                    max(diff): 0j                                                                                       
                    mean(diff): 0j                                                                                      
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

In [48]:
beta_tf = tf.constant(6.0)
x1, metrics1 = tfExpSU3.trainer.dynamics.apply_transition_hmc((xtf, beta_tf), eps=0.00001, nleapfrog=10)
x2, metrics2 = ptExpSU3.trainer.dynamics.apply_transition_hmc((xpt, 6.0), eps=0.00001, nleapfrog=10)

In [51]:
dynamics_tf = tfExpSU3.trainer.dynamics
dynamics_pt = ptExpSU3.trainer.dynamics

In [72]:
state_pt = dynamics_pt.random_state(6.0)
state_tf = State(
    tf.constant(grab_tensor(state_pt.x)),
    tf.constant(grab_tensor(state_pt.v)),
    tf.constant(6.0)
)
check_diff(state_pt.x, state_tf.x, name='x_init')
check_diff(state_pt.v, state_tf.v, name='v_init')
check_diff(state_pt.beta, state_tf.beta, name='beta')
check_diff(
    dynamics_pt.hamiltonian(state_pt),
    dynamics_tf.hamiltonian(state_tf),
    name='H init'
)

xtf_, metricstf_ = tfExpSU3.trainer.dynamics.apply_transition_hmc((state_tf.x, state_tf.beta), eps=0.00001, nleapfrog=10)
xpt_, metricspt_ = ptExpSU3.trainer.dynamics.apply_transition_hmc((state_pt.x, state_pt.beta), eps=0.00001, nleapfrog=10)

mcstates_tf = metricstf_.pop('mc_states')
mcstates_pt = metricspt_.pop('mc_states')

check_diff(xtf_, xpt_, name='x_out')
check_diff(metricstf_, metricspt_, name='metrics')

09:52:28 INFO     'x_init''                                                                                ]8;id=329418;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=238994;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): 0j                                                                                       
                    min(diff): 0j                                                                                       
                    max(diff): 0j                                                                                       
                    mean(diff): 0j                                                                                      
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'v_init''                                                                                ]8;id=653530;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=842027;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): 0j                                                                                       
                    min(diff): 0j                                                                                       
                    max(diff): 0j                                                                                       
                    mean(diff): 0j                                                                                      
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'beta''                                                                                  ]8;id=207817;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=363002;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): 0.0                                                                                      
                    min(diff): 0.0                                                                                      
                    max(diff): 0.0                                                                                      
                    mean(diff): 0.0                                                                                     
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'H init''                                                                                ]8;id=985428;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=985262;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): -1.7053025658242404e-13                                                                  
                    min(diff): -1.7053025658242404e-13                                                                  
                    max(diff): -1.7053025658242404e-13                                                                  
                    mean(diff): -1.7053025658242404e-13                                                                 
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

09:52:29 INFO     'x_out''                                                                                 ]8;id=546580;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=722523;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): (0.011849381076467458+0.018295709153826265j)                                             
                    min(diff): (-0.000314663308228047+9.861535145372358e-06j)                                           
                    max(diff): (0.00031223094983777455-4.440869622102106e-05j)                                          
                    mean(diff): (4.017937919266581e-08+6.203785927268563e-08j)                                          
                    std(diff): 9.408124370424699e-05                                                                    
                    np.allclose: False                                                                                  

...

         INFO     'logprob''                                                                               ]8;id=618432;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=516723;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): 6434.017167517397                                                                        
                    min(diff): 584.7860001735771                                                                        
                    max(diff): 585.0353020001401                                                                        
                    mean(diff): 584.9106515924906                                                                       
                    std(diff): 0.07883615995239178                                                                      
                    np.allclose: False                                                                                  

         INFO     'logdet''                                                                                ]8;id=54995;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=31288;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): 0.0                                                                                      
                    min(diff): 0.0                                                                                      
                    max(diff): 0.0                                                                                      
                    mean(diff): 0.0                                                                                     
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'acc''                                                                                   ]8;id=469841;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=845140;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): -0.15298023463194843                                                                     
                    min(diff): -0.15298023463194843                                                                     
                    max(diff): -0.15298023463194843                                                                     
                    mean(diff): -0.15298023463194843                                                                    
                    std(diff): 0.0                                                                                      
                    np.allclose: False                                                                                  

         INFO     'sumlogdet''                                                                             ]8;id=84072;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=868584;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): 0.0                                                                                      
                    min(diff): 0.0                                                                                      
                    max(diff): 0.0                                                                                      
                    mean(diff): 0.0                                                                                     
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO     'acc_mask''                                                                              ]8;id=307404;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=447109;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    sum(diff): -1.0                                                                                     
                    min(diff): -1.0                                                                                     
                    max(diff): -1.0                                                                                     
                    mean(diff): -1.0                                                                                    
                    std(diff): 0.0                                                                                      
                    np.allclose: False                                                                                  

In [ ]:
ketf = dynamics_tf.kinetic_energy(state_tf.v)
kept = dynamics_pt.kinetic_energy(state_pt.v)

In [65]:
check_diff(
    dynamics_tf.kinetic_energy(state_tf.v),
    dynamics_pt.kinetic_energy(state_pt.v)
)
check_diff(
    dynamics_tf.potential_energy(state_tf.x, state_tf.beta),
    dynamics_pt.potential_energy(state_pt.x, state_pt.beta)
)
check_diff(
    dynamics_tf.grad_potential(state_tf.x, state_tf.beta),
    dynamics_pt.grad_potential(state_pt.x, state_pt.beta)
)
check_diff(
    dynamics_tf.hamiltonian(state_tf),
    dynamics_pt.hamiltonian(state_pt)
)

09:44:56 INFO       sum(diff): 1.1368683772161603e-13                                                      ]8;id=384443;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=832632;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    min(diff): 1.1368683772161603e-13                                                                   
                    max(diff): 1.1368683772161603e-13                                                                   
                    mean(diff): 1.1368683772161603e-13                                                                  
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO       sum(diff): -2.2737367544323206e-13                                                     ]8;id=498928;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=68359;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    min(diff): -2.2737367544323206e-13                                                                  
                    max(diff): -2.2737367544323206e-13                                                                  
                    mean(diff): -2.2737367544323206e-13                                                                 
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

         INFO       sum(diff): (-2.7026991755718655e-14+6.793350604272774e-14j)                            ]8;id=960583;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=146819;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    min(diff): (-8.881784197001252e-16-8.881784197001252e-16j)                                          
                    max(diff): (1.7763568394002505e-15+0j)                                                              
                    mean(diff): (-9.164425915431944e-20+2.303517864404559e-19j)                                         
                    std(diff): 1.611295224201052e-16                                                                    
                    np.allclose: True                                                                                   

         INFO       sum(diff): -1.1368683772161603e-13                                                     ]8;id=931387;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py\common.py]8;;\:]8;id=949338;file:///lus/grand/projects/DLHMC/foremans/l2hmc-qcd/src/l2hmc/common.py#115\115]8;;\
                    min(diff): -1.1368683772161603e-13                                                                  
                    max(diff): -1.1368683772161603e-13                                                                  
                    mean(diff): -1.1368683772161603e-13                                                                 
                    std(diff): 0.0                                                                                      
                    np.allclose: True                                                                                   

In [ ]:
check_diff(metrics1, metrics2)

In [ ]:
k

In [ ]:
xtf = gtfutils.projectSU(xpt.numpy())

In [ ]:
run_hmc(tfExpSU3, beta=6.0, x=xtf, eps=0.0001, nleapfrog=10, nsteps=1000, nlog=1)

In [ ]:
run_hmc(ptExpSU3, beta=6.0, x=zpt, eps=0.0001, nleapfrog=16, nsteps=1000, nlog=1)

# OLD

In [ ]:
print(f'projectSU: {gtfutils.projectSU(Utf).numpy()}')

In [ ]:
gtfutils.projectSU(Utf).numpy()

In [ ]:
x1.shape

In [ ]:
data = ptExpSU3.dynamics.generate_proposal_hmc((ptState.x, ptState.beta), eps=0.001)

In [ ]:
data.keys()

In [ ]:
data['init'].x.shape
data['proposed'].x.shape

In [ ]:
data['metrics']['acc'].shape

In [ ]:
x1.shape

In [ ]:
x1_ = x1.reshape(xpt.shape)
x10 = x1_[0, 0, 0, 0, 0, 0]
x10

In [ ]:
pe = ptExpSU3.dynamics.potential_energy(xpt, torch.tensor(1.))

In [ ]:
pe.shape

In [ ]:
ke = ptExpSU3.dynamics.kinetic_energy(ptState.v)

In [ ]:
ke.shape

In [ ]:
x2_ = x2.reshape(xpt.shape)
x20 = x2_[0, 0, 0, 0, 0, 0]
x20

In [ ]:
(x20 - x10).real
(x20 - x10).imag

In [ ]:
metrics1['energy'].shape

In [ ]:
metrics1['energy'][1] - metrics1['energy'][0]

In [ ]:
metrics2['energy'][-1] - metrics1['energy'][-1]

In [ ]:
import l2hmc.group.tensorflow.utils as gtfutils
gtfutils.projectSU(Utf).numpy()

In [ ]:
g.checkU(Utf)

In [ ]:
gtfutils.checkU(Utf)

In [ ]:
checkSU(Utf)

In [ ]:
norm2_ = gtfutils.norm2(tf.linalg.adjoint(Utf) @ Utf - gtfutils.eyeOf(Utf))

In [ ]:
norm2_

In [ ]:
g.norm2(tf.linalg.adjoint(Utf) @ Utf - gtfutils.eyeOf(Utf))

In [ ]:
from 

In [ ]:
g.checkSU(tf.constant(xpt.numpy()))


In [ ]:
checkSU(tf.constant(xpt.numpy()))

In [ ]:
metrics1['energy'][0].shape

In [ ]:
metrics1['energy'].shape

In [ ]:
de = (metrics2['energy'] - metrics1['energy']).sum()

In [ ]:
run_hmc(ptExpSU3, beta=6.0, x=xpt, eps=0.0001, nleapfrog=16, nsteps=1000, nlog=1)

In [ ]:
run_hmc(exp_pt)

In [ ]:
run_hmc(exp_pt, beta=6.0, x=xpt)

In [ ]:
run_hmc(exp_tf, beta=6.0, x=xtf)

In [ ]:
%debug

In [ ]:
xpt[0].det()

In [ ]:
inputs_pt = (xpt, torch.tensor(1.0))
xpt_, hmetrics_pt = exp_pt.dynamics.apply_transition_hmc(inputs_pt, eps=torch.tensor(0.00001))

In [ ]:
inputs_tf = (xtf, tf.constant(1.0))
xtf_, hmetrics_tf = exp_tf.dynamics.apply_transition_hmc(inputs_tf, eps=tf.constant(0.000001))

In [ ]:
(xpt.numpy() - xtf.numpy()).sum()

In [ ]:
mcstates_pt = hmetrics_pt.pop('mc_states', None)
mcstates_tf = hmetrics_tf.pop('mc_states', None)
print('\n'.join([f'{key} (pt): {val.mean()}' for key, val in hmetrics_pt.items()]))
print(80 *'-')
print('\n'.join([f'{key} (tf): {val.numpy().mean()}' for key, val in hmetrics_tf.items()]))

In [ ]:
lmetrics_pt = lattice_pt.calc_metrics(x=xpt)

In [ ]:
lmetrics_tf = lattice_tf.calc_metrics(x=xtf)

In [ ]:
wlpt, _ = lattice_pt._wilson_loops(xpt, needs_rect=False)
wltf, _ = lattice_tf._wilson_loops(xtf, needs_rect=False)

In [ ]:
dwl = (wlpt.numpy() - wltf.numpy())

In [ ]:
(dwl ** 2).sum()

In [ ]:
qpt = wlpt.imag.sum(tuple(range(2, len(wlpt.shape)))).sum(0)
qtf = tf.reduce_sum(
    tf.reduce_sum(tf.math.imag(wltf), axis=range(2, len(wltf.shape))),
    axis=0
)
qpt /= (32 * (np.pi ** 2))
qtf /= (32 * (np.pi ** 2))

In [ ]:
qpt.numpy()

In [ ]:
qtf.numpy()

In [ ]:
((qpt.numpy() - qtf.numpy()) ** 2).sum()

In [ ]:
xpt_ = lattice_pt.g.compat_proj(xpt)
xtf_ = lattice_tf.g.compat_proj(xtf)

In [ ]:
xpt_[0, 0, 0, 0, 0, 0].numpy()
xtf_[0, 0, 0, 0, 0, 0].numpy()

In [ ]:
xpt_2 = xpt_.adjoint() @ xpt_
xtf_2 = tf.linalg.adjoint(xtf_) @ xtf_

In [ ]:
((xpt_2.numpy() - xtf_2.numpy()) ** 2).sum()

In [ ]:
((xpt_.numpy() - xtf_.numpy()) ** 2).sum()

In [ ]:
diffs = {}
for key, val in lmetrics_pt.items():
    vpt = val.numpy()
    vtf = lmetrics_tf[key].numpy()
    diffs[key] = ((vpt - vtf) ** 2).sum()
    
print(f'\n'.join([f'{k}: {v}' for k, v in diffs.items()]))

In [ ]:
lattice_pt.g.trace(xpt.adjoint() @ xpt).sum()

In [ ]:
lattice_tf.g.trace(tf.m)

In [ ]:
xpt_.shape

In [ ]:
wlpt, _ = lattice_pt._wilson_loops(xpt, needs_rect=False)
wltf, _ = lattice_tf._wilson_loops(xtf, needs_rect=False)

In [ ]:
wlpt.shape

In [ ]:
pspt = wlpt.real.sum(tuple(range(2, len(wlpt.shape))))
pspt.shape

In [ ]:
wltf, _ = lattice_tf._wilson_loops(xtf, needs_rect=False)

In [ ]:
(wlpt.numpy() - wltf.numpy()).sum()

In [ ]:
qsin_pt = lattice_pt.sin_charges(xpt)
qsin_tf = lattice_tf.sin_charges(xtf)
(qsin_pt.numpy() - qsin_tf.numpy()).sum()

In [ ]:
qint_pt = lattice_pt.int_charges

In [ ]:
plaqs_tf = lattice_tf._plaquettes(xtf)

In [ ]:
plaqs_pt = lattice_pt._plaquettes(xpt)

In [ ]:
plaqs_pt.shape

In [ ]:
plaqs_tf.shape

In [ ]:
wltf.shape

In [ ]:
ps, _ = lattice_pt._wilson_loops(xpt_)

In [ ]:
ps.shape

In [ ]:
qsinpt_ = lattice_pt.sin_charges(xpt_)

In [ ]:
qintpt_ = lattice_pt.int_charges(xpt_)

In [ ]:
qsinpt_.shape

In [ ]:
qsinpt_

In [ ]:
qintpt_

In [ ]:
xpt_.shape

In [ ]:
hmetrics_pt.keys()

In [ ]:
hmetrics_pt['acc']

In [ ]:
hmetrics_pt['sumlogdet']

In [ ]:
xout, metrics = trainer_pt.hmc_step(inputs_pt, eps=torch.tensor(0.0001))

In [ ]:
inputs_tf = (xtf, tf.constant(1.0))
xout_tf, metrics_tf = trainer_tf.hmc_step(inputs_tf, eps=tf.constant(0.0001))

In [ ]:
xtf_.shape

In [ ]:
xtf_, metrics_tf = dynamics_tf(inputs_tf)

In [ ]:
xtf_, metrics_tf = dynamics_tf(inputs_tf)

In [ ]:
%debug

In [ ]:
cfg = compose('config.yaml', overrides=['framework=pytorch'])

In [ ]:
%debug

In [ ]:
GlobalHydra.instance().clear()
conf_dir = CONF_DIR.resolve().absolute().as_posix()
initialize_config_dir(conf_dir)
cfg = compose('config')  # , overrides=overrides)

In [ ]:
cfg = get_cfg([])

In [ ]:
conf = compose(config_name='config')

In [ ]:
#print_config(OmegaConf.to_object('../conf/config.yaml'))

In [ ]:
latpt = LatticeSU3pt(5, (4, 4, 4, 4))
lattf = LatticeSU3tf(5, (4, 4, 4, 4))

In [ ]:
xpt = latpt.random()
xnp = xpt.numpy()
xtf = tf.constant(xnp)

In [ ]:
wlpt = latpt.wilson_loops(xpt)
wltf = lattf.wilson_loops(xtf)

In [ ]:
(wlpt.numpy() - wltf.numpy()).sum()

In [ ]:
plaqs_pt = latpt._plaquettes(xpt)
plaqs_tf = lattf._plaquettes(xtf)

In [ ]:
(plaqs_pt.numpy() - plaqs_tf.numpy()).sum()

In [ ]:
qint_pt = latpt._int_charges(wlpt)
qint_tf = lattf._int_charges(wltf)

In [ ]:
(qint_pt.numpy() - qint_tf.numpy()).sum()

In [ ]:
charges_pt = latpt.charges(xpt)
charges_tf = lattf.charges(xtf)

In [ ]:
(charges_pt['qint'].numpy() - charges_tf['qint'].numpy()).sum()

In [ ]:
(charges_pt['qsin'].numpy() - charges_tf['qsin'].numpy()).sum()

In [ ]:
from l2hmc.configs import DynamicsConfig
from l2hmc.dynamics.pytorch.dynamics import Dynamics as ptDynamics
from l2hmc.dynamics.tensorflow.dynamics import Dynamics as tfDynamics

In [ ]:
from __future__ import absolute_import, print_function, annotations, division
import os
import hydra

from typing import Optional
from pathlib import Path

from omegaconf import OmegaConf
from hydra import (
    initialize,
    initialize_config_module,
    initialize_config_dir,
    compose
)

from l2hmc.common import get_timestamp
from l2hmc.configs import CONF_DIR
from l2hmc.experiment import Experiment
from hydra.core.global_hydra import GlobalHydra

from l2hmc.utils.rich import print_config


In [ ]:
GlobalHydra.instance().clear()
initialize(config_path="../conf/")
cfg = compose('config', overrides=['mode=debug', 'framework=pytorch'])
#conf = OmegaConf.load('../conf/config.yaml')
print_config(conf)

In [ ]:
%debug

In [ ]:
GlobalHydra.instance().clear()
initialize(config_path='../conf/') # Assume the configuration file is in the current folder
cfg = compose('config', strict=False)
#cfg = compose('config', return_hydra_config=True)
print_config(cfg)

In [ ]:
def get_experiment():
    with initialize_config_dir(CONF_DIR):
        cfg = compose(config_name='config.yaml', overrides=overrides)
        print(OmegaConf.to_yaml(cfg, resolve=True))
        #cfile = outdir.joinpath('config.yaml')
        #assert callable(main)
        #output = main(cfg)
        return Experiment(cfg)

    #print(f'Saving config to: {cfile}')
    #with open(cfile, 'w') as f:
    #    f.write(OmegaConf.to_yaml(cfg, resolve=True))

In [ ]:

#initialize(config_path='../conf')  # , job_name="test_app")
initialize_config_dir(CONF_DIR.as_posix())
#cfg = compose(config_name="config")  # , overrides=['dynamics=su3', 'framework=pytorch'])
#print_config(cfg)
#print(OmegaConf.to_yaml(cfg))
#cfg = compose(config_name='config.yaml')

In [ ]:
GlobalHydra.instance().clear()
#with initialize(config_path="../conf/"):
with initialize_config_dir(CONF_DIR.as_posix()):
    cfg = compose(config_name='config') #, overrides=['mode=debug', 'framework=pytorch'])
    print(OmegaConf.to_yaml(cfg))
    #experiment = Experiment(cfg)

In [ ]:
from l2hmc.configs import ExperimentConfig
schema = OmegaConf.structured(ExperimentConfig)
conf = OmegaConf.load("../conf/config.yaml")
#with raises(ValidationError):
cfg = OmegaConf.merge(schema, conf)

In [ ]:
from hydra import initialize, compose
GlobalHydra.instance().clear()
initialize(config_path='../') # Assume the configuration file is in the current folder
cfg = compose()
#cfg = compose(config_name='config', overrides=['framework=pytorch', 'mode=debug'])

In [ ]:
cfg = compose(config_name='config.yaml')  # , overrides=['dynamics=su3', 'framework=pytorch'])

In [ ]:
from omegaconf import DictConfig, OmegaConf

cfg = OmegaConf.load(CONF_DIR.joinpath('config.yaml').as_posix())
cfg = DictConfig()